# Beispiel für die Datenverarbeitung der Smartphone Sensordaten

Das folgende Beispiel zeigt die Verarbeitung der Sensordaten, welche im Projekt SMANCY an bestimmten Punkten in Köln, Detmold, Hahn und Paderborn aufgenommen wurden.

Das Beispiel zeigt die grundlegende Verarbeitung der Sensordaten zu einer Zeitserie mit 1sek Intervall.

## Bemerkung
Das Projekt SMANCY hat gezeigt, dass die Sensordaten des Smartphones derzeit nicht genau genug für eine hinreichende Kollisionsvorhersage zwischen Fußgänger und anderem Verkehrsteilnehmer sind.
Die Daten dienen als Beispiel für die schlechte Qualität der Positionsdaten in Städten, wie z.B. Köln. In ländlichen Gegenden sind die Positionsgenauigkeiten besser, aber immer noch nicht ausreichend.


In [56]:
import pandas as pd
import numpy as np
import datetime
import pyproj
import math

from pyquaternion import Quaternion
from geopy.distance import great_circle

## Daten auslesen und Zeitindex setzen

In [207]:
%ls

20180221_PF_HNI_FHDW.ipynb
mcloud.zip
sensor_20180224.172514_AmRossbruch.log
sensor_20180301.054402_zurArbeit.log
sensor_20180327.115413_Koeln_Neumarkt.log
sensor_20180327.124801_Koeln_Barbarossa.log
sensor_20180327.130934_Koeln_Hohenstaufenring.log
sensor_20180403.105447_Gebaeudeumrundung.log
sensor_20180403.142537_PB.log
smacy_example.ipynb


In [208]:
data_file="sensor_20180327.115413_Koeln_Neumarkt.log"

In [209]:
colnames = ["timestamp", "tag", "val_0", "val_1", "val_2", "val_3", "val_4", "val_5", "val_6"]

In [210]:
df = pd.read_csv(data_file, sep=";",decimal=",", names=colnames)

In [211]:
df["time"] = df.timestamp.apply(lambda x: datetime.datetime.fromtimestamp(x*1e-9))
df = df.set_index("time")
del df["timestamp"]

In [212]:
df

tag     val_0      val_1      val_2  \
time                                                                           
2018-03-27 11:54:13.066978  SMgr_Orientation  0.000000   0.000000   0.000000   
2018-03-27 11:54:13.066978     accelerometer -5.703163   7.853221   5.985687   
2018-03-27 11:54:13.053736  SMgr_Orientation  1.638128  -0.759694   0.761232   
2018-03-27 11:54:13.053736    magnetic_field  1.800000 -28.200001 -36.100002   
2018-03-27 11:54:13.081765         gyroscope  0.486249  -0.774577  -0.113621   
...                                      ...       ...        ...        ...   
2018-03-27 12:05:41.657914         gyroscope  0.047647   0.020769  -0.062308   
2018-03-27 12:05:39.734469          DGPS-NED  5.021000   2.374000   3.675000   
2018-03-27 12:05:41.645125  SMgr_Orientation -2.278155  -0.449837   0.103192   
2018-03-27 12:05:41.645125     accelerometer -0.919402   4.309695   8.877971   
2018-03-27 12:05:41.659913         gyroscope  0.032987   0.018326  -0.059865   

                            val_3  val_4  val_5  val_6  
time                                                    
2018-03-27 11:54:13.066978    NaN    NaN    NaN    NaN  
2018-03-27 11:54:13.066978    NaN    NaN    NaN    NaN  
2018-03-27 11:54:13.053736    NaN    NaN    NaN    NaN  
2018-03-27 11:54:13.053736    NaN    NaN    NaN    NaN  
2018-03-27 11:54:13.081765    NaN    NaN    NaN    NaN  
...                           ...    ...    ...    ...  
2018-03-27 12:05:41.657914    NaN    NaN    NaN    NaN  
2018-03-27 12:05:39.734469  0.405  0.808    NaN    NaN  
2018-03-27 12:05:41.645125    NaN    NaN    NaN    NaN  
2018-03-27 12:05:41.645125    NaN    NaN    NaN    NaN  
2018-03-27 12:05:41.659913    NaN    NaN    NaN    NaN  

[294320 rows x 8 columns]

## Sensordaten in Spaltform transformieren

In [213]:
df_val = df.pivot_table(index="time", columns="tag")
df_val = df_val.swaplevel(1,0, axis=1).sort_index(level=0, axis=1)

In [214]:
df_val

tag                        DGPS-LLH                         DGPS-NED         \
                              val_0 val_1 val_2 val_3 val_4    val_0  val_1   
time                                                                          
2018-03-27 11:54:13.039053      NaN   NaN   NaN   NaN   NaN   -0.782  0.487   
2018-03-27 11:54:13.053736      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 11:54:13.054745      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 11:54:13.063746      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 11:54:13.064755      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
...                             ...   ...   ...   ...   ...      ...    ...   
2018-03-27 12:05:41.651908      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 12:05:41.653910      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 12:05:41.655912      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 12:05:41.657914      NaN   NaN   NaN   NaN   NaN      NaN    NaN   
2018-03-27 12:05:41.659913      NaN   NaN   NaN   NaN   NaN      NaN    NaN   

tag                                              ... magnetic_field pressure  \
                            val_2  val_3  val_4  ...          val_2    val_0   
time                                             ...                           
2018-03-27 11:54:13.039053  1.794  0.382  0.788  ...            NaN      NaN   
2018-03-27 11:54:13.053736    NaN    NaN    NaN  ...     -36.100002      NaN   
2018-03-27 11:54:13.054745    NaN    NaN    NaN  ...            NaN      NaN   
2018-03-27 11:54:13.063746    NaN    NaN    NaN  ...     -36.000000      NaN   
2018-03-27 11:54:13.064755    NaN    NaN    NaN  ...            NaN      NaN   
...                           ...    ...    ...  ...            ...      ...   
2018-03-27 12:05:41.651908    NaN    NaN    NaN  ...            NaN      NaN   
2018-03-27 12:05:41.653910    NaN    NaN    NaN  ...            NaN      NaN   
2018-03-27 12:05:41.655912    NaN    NaN    NaN  ...            NaN      NaN   
2018-03-27 12:05:41.657914    NaN    NaN    NaN  ...            NaN      NaN   
2018-03-27 12:05:41.659913    NaN    NaN    NaN  ...            NaN      NaN   

tag                                    rotation_vector                    \
                           val_1 val_2           val_0 val_1 val_2 val_3   
time                                                                       
2018-03-27 11:54:13.039053   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 11:54:13.053736   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 11:54:13.054745   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 11:54:13.063746   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 11:54:13.064755   NaN   NaN             NaN   NaN   NaN   NaN   
...                          ...   ...             ...   ...   ...   ...   
2018-03-27 12:05:41.651908   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 12:05:41.653910   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 12:05:41.655912   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 12:05:41.657914   NaN   NaN             NaN   NaN   NaN   NaN   
2018-03-27 12:05:41.659913   NaN   NaN             NaN   NaN   NaN   NaN   

tag                              step_detector  
                           val_4         val_0  
time                                            
2018-03-27 11:54:13.039053   NaN           NaN  
2018-03-27 11:54:13.053736   NaN           NaN  
2018-03-27 11:54:13.054745   NaN           NaN  
2018-03-27 11:54:13.063746   NaN           NaN  
2018-03-27 11:54:13.064755   NaN           NaN  
...                          ...           ...  
2018-03-27 12:05:41.651908   NaN           NaN  
2018-03-27 12:05:41.653910   NaN           NaN  
2018-03-27 12:05:41.655912   NaN           NaN  
2018-03-27 12:05:41.657914   NaN           NaN  
2018-03-27 12:05:41.659913   NaN           NaN  

[181874 rows x 66 co

## Resampling der Sensordaten in 1s Intervall


In [232]:
df_sampled = df_val.resample("1s").mean()

In [233]:
df_sampled

tag                   DGPS-LLH                                            \
                         val_0     val_1       val_2     val_3     val_4   
time                                                                       
2018-03-27 11:54:13  50.936085  6.947051  100.738761  0.381667  0.787444   
2018-03-27 11:54:14  50.936091  6.947061  100.595685  0.380700  0.785800   
2018-03-27 11:54:15  50.936097  6.947075  100.528947  0.379700  0.784700   
2018-03-27 11:54:16  50.936102  6.947089  100.514144  0.378875  0.783750   
2018-03-27 11:54:17  50.936109  6.947104  100.392056  0.377750  0.782750   
...                        ...       ...         ...       ...       ...   
2018-03-27 12:05:37  50.936133  6.947074   99.734584  0.413167  0.817917   
2018-03-27 12:05:38  50.936136  6.947075   99.360920  0.409100  0.813200   
2018-03-27 12:05:39  50.936135  6.947075   99.045379  0.406500  0.809750   
2018-03-27 12:05:40        NaN       NaN         NaN       NaN       NaN   
2018-03-27 12:05:41        NaN       NaN         NaN       NaN       NaN   

tag                  DGPS-NED                                          ...  \
                        val_0     val_1     val_2     val_3     val_4  ...   
time                                                                   ...   
2018-03-27 11:54:13 -0.452200  0.667700  1.830400  0.381700  0.787500  ...   
2018-03-27 11:54:14  0.234300  1.418700  1.977500  0.380700  0.785800  ...   
2018-03-27 11:54:15  0.835900  2.399800  2.044200  0.379700  0.784700  ...   
2018-03-27 11:54:16  1.398250  3.363000  2.059125  0.378875  0.783750  ...   
2018-03-27 11:54:17  2.230167  4.435833  2.180917  0.377750  0.782750  ...   
...                       ...       ...       ...       ...       ...  ...   
2018-03-27 12:05:37  4.954917  2.321333  2.838500  0.413167  0.817917  ...   
2018-03-27 12:05:38  5.171600  2.402900  3.212200  0.409100  0.813200  ...   
2018-03-27 12:05:39  5.087375  2.391375  3.527750  0.406500  0.809750  ...   
2018-03-27 12:05:40       NaN       NaN       NaN       NaN       NaN  ...   
2018-03-27 12:05:41       NaN       NaN       NaN       NaN       NaN  ...   

tag                 magnetic_field     pressure                  \
                             val_2        val_0     val_1 val_2   
time                                                              
2018-03-27 11:54:13     -40.129475  1004.427588  0.170125   0.0   
2018-03-27 11:54:14     -44.260001  1004.469556 -0.163711   0.0   
2018-03-27 11:54:15     -43.726001  1004.464014 -0.119628   0.0   
2018-03-27 11:54:16     -42.353704  1004.432764  0.128953   0.0   
2018-03-27 11:54:17     -40.727587  1004.458252 -0.073797   0.0   
...                            ...          ...       ...   ...   
2018-03-27 12:05:37     -28.770000  1004.190723  2.054558   0.0   
2018-03-27 12:05:38     -28.883000  1004.185058  2.099625   0.0   
2018-03-27 12:05:39     -29.650000  1004.183521  2.111863   0.0   
2018-03-27 12:05:40     -30.577000  1004.183374  2.113028   0.0   
2018-03-27 12:05:41     -30.969841  1004.177368  2.160816   0.0   

tag                 rotation_vector                                       \
                              val_0     val_1     val_2     val_3  val_4   
time                                                                       
2018-03-27 11:54:13        0.425177 -0.050187 -0.410838  0.799498  246.0   
2018-03-27 11:54:14        0.272785 -0.105330 -0.497273  0.815127  246.0   
2018-03-27 11:54:15        0.367290 -0.081350 -0.466166  0.799078  246.0   
2018-03-27 11:54:16        0.381131 -0.106152 -0.497179  0.770847  246.0   
2018-03-27 11:54:17        0.243138 -0.148161 -0.439855  0.850764  246.0   
...                             ...       ...       ...       ...    ...   
2018-03-27 12:05:37        0.017806  0.248312  0.890927  0.379617  246.0   
2018-03-27 12:05:38        0.006999  0.242993  0.899524  0.362599  246.0   
2018-03-27 12:05:39       -0.000982  0.229046  0.903362  0.362558  

# Hilfsvariablen zum einfachen Zugriff auf die Daten


In [219]:
# Hilfsvariablen zum einfachen Zugriff auf die Daten

## GPS Lat und lon Positionen vom Smartphone
GPS_LAT = ("GPS-LLH","val_0")
GPS_LON = ("GPS-LLH","val_1")
GPS_LATLON = [GPS_LAT, GPS_LON]
GPS_ALT = ("GPS-LLH","val_2")
GPS_ACC = ("GPS-LLH","val_3")
GPS_VEL = ("GPS-LLH","val_4")

## DGPS Positionen
DGPS_LAT = ("DGPS-LLH","val_0")
DGPS_LON = ("DGPS-LLH","val_1")
DGPS_LATLON = [DGPS_LAT, DGPS_LON]
DGPS_ALT = ("DGPS-LLH","val_2")
DGPS_ACC = ("DGPS-LLH","val_3")
DGPS_VEL = ("DGPS-LLH","val_4")

# Android Sensor Daten (1:1 loggin der Daten)
## Details unter https://developer.android.com/reference/android/hardware/SensorManager

## Höhe über NN auf Basis der Luftdruckdaten
SMGR_ALT = ("SMgr_Altitude","val_0")

## Orientierung als Rotation in Radians
SMGR_ORIENTATION_YAW = ("SMgr_Orientation","val_0")
SMGR_ORIENTATION_PITCH = ("SMgr_Orientation","val_1")
SMGR_ORIENTATION_ROLL = ("SMgr_Orientation","val_2")

# Orientierung als Quaternion in X,Y,Z und Angle
SMGR_QUAT_X = ("SMgr_Quaternion","val_0")
SMGR_QUAT_Y = ("SMgr_Quaternion","val_1")
SMGR_QUAT_Z = ("SMgr_Quaternion","val_2")
SMGR_QUAT_A = ("SMgr_Quaternion","val_3")

# Beschleunigung in X,Y und Z Richtung
ACC_X = ("accelerometer", "val_0")
ACC_Y = ("accelerometer", "val_1")
ACC_Z = ("accelerometer", "val_2")

# rotation vector
# https://developer.android.com/guide/topics/sensors/sensors_motion#sensors-motion-rotate
ROT_X = ("rotation_vector", "val_0")
ROT_Y = ("rotation_vector", "val_1")
ROT_Z = ("rotation_vector", "val_2")

# Game rotation vector (entsprich Rotation vector ohne berücksichtigung des mag. Feldes)
# https://developer.android.com/guide/topics/sensors/sensors_motion#sensors-motion-rotate
GROT_X = ("game_rotation_vector", "val_0")
GROT_Y = ("game_rotation_vector", "val_1")
GROT_Z = ("game_rotation_vector", "val_2")

# Gravity Vector
GRAV_X = ("gravity", "val_0")
GRAV_Y = ("gravity", "val_1")
GRAV_Z = ("gravity", "val_2")

# Gyroscope
# angular speed um x,y,z Achse
GYRO_X = ("gyroscope", "val_0")
GYRO_Y = ("gyroscope", "val_1")
GYRO_Z = ("gyroscope", "val_2")

# Lichtsensor
LIGHT_LUX = ("gyroscope", "val_2")

# linear acceleration
# https://developer.android.com/reference/android/hardware/SensorEvent#values
ACC_X = ("linear_acceleration", "val_0")
ACC_Y = ("linear_acceleration", "val_1")
ACC_Z = ("linear_acceleration", "val_2")

# magnetic field in micro-Tesla along x,y,z axis
MAG_X = ("magnetic_field", "val_0")
MAG_Y = ("magnetic_field", "val_1")
MAG_Z = ("magnetic_field", "val_2")

# Pressure  Atmospheric pressure in hPa (millibar) 
PRESSURE = ("pressure", "val_0")


In [220]:
df_sampled[[GPS_LAT, GPS_LON, DGPS_LAT, DGPS_LON]]

tag                    GPS-LLH             DGPS-LLH          
                         val_0     val_1      val_0     val_1
time                                                         
2018-03-27 11:54:13  50.936074  6.947076  50.936085  6.947051
2018-03-27 11:54:14  50.936077  6.947081  50.936091  6.947061
2018-03-27 11:54:15  50.936077  6.947091  50.936097  6.947075
2018-03-27 11:54:16  50.936079  6.947110  50.936102  6.947089
2018-03-27 11:54:17  50.936082  6.947120  50.936109  6.947104
...                        ...       ...        ...       ...
2018-03-27 12:05:37  50.936057  6.947034  50.936133  6.947074
2018-03-27 12:05:38  50.936057  6.947034  50.936136  6.947075
2018-03-27 12:05:39  50.936057  6.947035  50.936135  6.947075
2018-03-27 12:05:40        NaN       NaN        NaN       NaN
2018-03-27 12:05:41        NaN       NaN        NaN       NaN

[689 rows x 4 columns]

# Interpolation der GPS Werte

In [234]:
df_interpolated = df_sampled.interpolate(method="linear")

In [235]:
df_interpolated[GPS_LATLON]

tag                    GPS-LLH          
                         val_0     val_1
time                                    
2018-03-27 11:54:13  50.936074  6.947076
2018-03-27 11:54:14  50.936077  6.947081
2018-03-27 11:54:15  50.936077  6.947091
2018-03-27 11:54:16  50.936079  6.947110
2018-03-27 11:54:17  50.936082  6.947120
...                        ...       ...
2018-03-27 12:05:37  50.936057  6.947034
2018-03-27 12:05:38  50.936057  6.947034
2018-03-27 12:05:39  50.936057  6.947035
2018-03-27 12:05:40  50.936057  6.947035
2018-03-27 12:05:41  50.936057  6.947035

[689 rows x 2 columns]

In [224]:
df_interpolated[GPS_LATLON].mean().values

array([50.93600967,  6.94737051])

# Visualisierung der GPS Daten in eine Map

In [236]:
gps_points = df_interpolated[GPS_LATLON].dropna().values


In [237]:
import folium


m = folium.Map(location=df_interpolated[GPS_LATLON].mean().values, zoom_start=18)

folium.PolyLine(gps_points, color="blue", weight=2.5, opacity=1).add_to(m)

m